In [18]:
import tensorflow as tf
# physical_devices = tf.config.list_physical_devices('GPU') 
# tf.config.experimental.set_memory_growth(physical_devices[0], True)

# Import libraries
import pandas as pd
import numpy as np
from tensorflow import keras
from keras.models import Sequential
from keras.layers import Dense, Dropout, LeakyReLU, BatchNormalization, GaussianNoise
from keras.callbacks import ModelCheckpoint, ReduceLROnPlateau, EarlyStopping
from tensorflow.keras.optimizers import SGD
from keras.wrappers.scikit_learn import KerasClassifier
from keras.constraints import maxnorm
from keras.regularizers import l1
from tensorflow.keras import initializers
# Random weights kernel_initializer=initializers.RandomNormal(stddev=0.01), 

# Preprocessing
from sklearn.preprocessing import MinMaxScaler, RobustScaler, StandardScaler, Normalizer
from sklearn.impute import SimpleImputer
from sklearn.model_selection import train_test_split

# Evaluating
from sklearn.model_selection import GridSearchCV, train_test_split
import matplotlib.pyplot as plt

# Saving model
from keras.models import load_model

imputer = SimpleImputer()
MMS = MinMaxScaler()
RS = RobustScaler()
SS = StandardScaler()
Norm = Normalizer()

# Read data
data = pd.read_csv('./data/DF_with_commodities.csv')
data2 = pd.read_csv('./data/Normalized_df_with_commodities.csv')

In [19]:
# Load Data

y = data['Close']
x = data.drop(['Close'], axis=1)
y2 = data2['Close']
x2 = data2.drop(['Close'], axis=1)

In [24]:
# Split Data

x_train, x_test, y_train, y_test = train_test_split(x2, y2, test_size=0.3, shuffle=False)

In [25]:
x_train

Date    Volume      Open      High       Low      SMA7       ADX  \
0     0.000000  0.006522  0.035294  0.034884  0.036145  0.027444  0.198734   
1     0.000130  0.008047  0.035294  0.034884  0.036145  0.027444  0.193733   
2     0.000261  0.031155  0.035294  0.034884  0.036145  0.027444  0.189089   
3     0.000391  0.021421  0.035294  0.034884  0.036145  0.027444  0.184777   
4     0.000782  0.033337  0.035294  0.034884  0.036145  0.027444  0.180773   
...        ...       ...       ...       ...       ...       ...       ...   
3724  0.698775  0.087016  0.317647  0.325581  0.325301  0.329331  0.242737   
3725  0.698905  0.073708  0.329412  0.325581  0.325301  0.325901  0.243390   
3726  0.699035  0.109748  0.329412  0.337209  0.337349  0.325901  0.231861   
3727  0.699166  0.059136  0.341176  0.337209  0.337349  0.325901  0.221156   
3728  0.699296  0.032793  0.329412  0.325581  0.337349  0.327616  0.211216   

            MI       ATR       OBV  ...    mqg.ax    anz.ax    shl.ax  \
0     0.700015  0.075949  0.662183  ...  0.016625  0.015532  0.046633   
1     0.697291  0.075949  0.662183  ...  0.016682  0.015812  0.045457   
2     0.662664  0.063291  0.662183  ...  0.017096  0.016067  0.044710   
3     0.618078  0.050633  0.662183  ...  0.017340  0.017865  0.044710   
4     0.589015  0.037975  0.662183  ...  0.017096  0.014792  0.045778   
...        ...       ...       ...  ...       ...       ...       ...   
3724  0.672996  0.189873  0.132454  ...  0.233422  0.592628  0.320485   
3725  0.668754  0.189873  0.148206  ...  0.237961  0.616083  0.319574   
3726  0.671458  0.189873  0.171660  ...  0.248329  0.644973  0.317900   
3727  0.672355  0.189873  0.159022  ...  0.243090  0.619516  0.312322   
3728  0.666489  0.164557  0.159022  ...  0.242647  0.615797  0.308417   

        brg.ax    qbe.ax    ncm.ax    cpu.ax    wbc.ax    wow.ax    tls.ax  
0     0.003440  0.154618  0.021632  0.224927  0.018858  0.010471  0.158416  
1     0.003557  0.155093  0.021235  0.231904  0.016193  0.008623  0.156256  
2     0.003557  0.150959  0.020402  0.234189  0.016046  0.008869  0.164894  
3     0.003322  0.153216  0.020441  0.238634  0.015957  0.004804  0.174251  
4     0.003440  0.149390  0.020044  0.228323  0.013690  0.003080  0.177131  
...        ...       ...       ...       ...       ...       ...       ...  
3724  0.151344  0.499368  0.223292  0.389688  0.722813  0.435536  0.845918  
3725  0.151859  0.510771  0.228101  0.391856  0.744656  0.435746  0.862434  
3726  0.153663  0.529929  0.231644  0.402696  0.783790  0.451036  0.885143  
3727  0.150571  0.516245  0.218484  0.402262  0.751936  0.438976  0.850047  
3728  0.145676  0.517614  0.211651  0.403563  0.744049  0.438545  0.835596  

[3729 rows x 43 columns]

In [ ]:


model = Sequential()
model.add(Dense(216, input_dim=x.shape[1], activation='relu'))
model.add(Dense(532, activation='relu'))
model.add(Dense(216, activation='relu'))
model.add(Dense(108, activation='relu'))
model.add(Dense(54, activation='relu'))
model.add(Dense(27, activation='relu'))
model.add(Dense(13, activation='relu'))
model.add(Dense(4, activation='relu'))
model.add(Dense(1, activation='sigmoid'))

sgd = SGD(lr=0.0001, momentum=0)
# model.compile(loss='binary_crossentropy', optimizer='adam', metrics=['accuracy'])

model.compile(loss='squared_hinge', optimizer=sgd, metrics=['accuracy'])

# LEARNING RATE SCHEDULE
rlrp = ReduceLROnPlateau(monitor='val_accuracy', factor=0.1, patience=5, min_delta=1E-7, verbose=1)
# Early Stopping
es = EarlyStopping(monitor='val_loss', mode='min', verbose=1, patience=10)
model.fit(x2, y2, epochs=2000000, batch_size=100, validation_split=0.3, verbose=1, callbacks=[rlrp])

/home/dev/anaconda3/envs/sbtrader/lib/python3.9/site-packages/keras/optimizer_v2/gradient_descent.py:102: UserWarning: The `lr` argument is deprecated, use `learning_rate` instead.
  super(SGD, self).__init__(name, **kwargs)


Epoch 1/2000000
38/38 [==============================] - 1s 7ms/step - loss: 0.7942 - accuracy: 0.0000e+00 - val_loss: 0.4559 - val_accuracy: 6.2539e-04 - lr: 1.0000e-04
Epoch 2/2000000
38/38 [==============================] - 0s 4ms/step - loss: 0.7939 - accuracy: 0.0000e+00 - val_loss: 0.4554 - val_accuracy: 6.2539e-04 - lr: 1.0000e-04
Epoch 3/2000000
38/38 [==============================] - 0s 4ms/step - loss: 0.7937 - accuracy: 0.0000e+00 - val_loss: 0.4549 - val_accuracy: 6.2539e-04 - lr: 1.0000e-04
Epoch 4/2000000
38/38 [==============================] - 0s 4ms/step - loss: 0.7934 - accuracy: 0.0000e+00 - val_loss: 0.4543 - val_accuracy: 6.2539e-04 - lr: 1.0000e-04
Epoch 5/2000000
38/38 [==============================] - 0s 4ms/step - loss: 0.7932 - accuracy: 0.0000e+00 - val_loss: 0.4538 - val_accuracy: 6.2539e-04 - lr: 1.0000e-04
Epoch 6/2000000
19/38 [==============>...............] - ETA: 0s - loss: 0.7898 - accuracy: 0.0000e+00
Epoch 00006: ReduceLROnPlateau reducing learnin

IOPub message rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_msg_rate_limit`.

Current values:
ServerApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
ServerApp.rate_limit_window=3.0 (secs)



38/38 [==============================] - 0s 3ms/step - loss: 0.7927 - accuracy: 0.0000e+00 - val_loss: 0.4530 - val_accuracy: 6.2539e-04 - lr: 0.0000e+00
Epoch 20057/2000000
38/38 [==============================] - 0s 13ms/step - loss: 0.7927 - accuracy: 0.0000e+00 - val_loss: 0.4530 - val_accuracy: 6.2539e-04 - lr: 0.0000e+00
Epoch 20058/2000000
38/38 [==============================] - 0s 13ms/step - loss: 0.7927 - accuracy: 0.0000e+00 - val_loss: 0.4530 - val_accuracy: 6.2539e-04 - lr: 0.0000e+00
Epoch 20059/2000000
38/38 [==============================] - 0s 3ms/step - loss: 0.7927 - accuracy: 0.0000e+00 - val_loss: 0.4530 - val_accuracy: 6.2539e-04 - lr: 0.0000e+00
Epoch 20060/2000000
38/38 [==============================] - 0s 3ms/step - loss: 0.7927 - accuracy: 0.0000e+00 - val_loss: 0.4530 - val_accuracy: 6.2539e-04 - lr: 0.0000e+00
Epoch 20061/2000000
38/38 [==============================] - 0s 3ms/step - loss: 0.7927 - accuracy: 0.0000e+00 - val_loss: 0.4530 - val_accuracy: 6.

IOPub message rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_msg_rate_limit`.

Current values:
ServerApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
ServerApp.rate_limit_window=3.0 (secs)



Epoch 23713/2000000
38/38 [==============================] - 0s 3ms/step - loss: 0.7927 - accuracy: 0.0000e+00 - val_loss: 0.4530 - val_accuracy: 6.2539e-04 - lr: 0.0000e+00
Epoch 23714/2000000
38/38 [==============================] - 0s 3ms/step - loss: 0.7927 - accuracy: 0.0000e+00 - val_loss: 0.4530 - val_accuracy: 6.2539e-04 - lr: 0.0000e+00
Epoch 23715/2000000
38/38 [==============================] - 0s 3ms/step - loss: 0.7927 - accuracy: 0.0000e+00 - val_loss: 0.4530 - val_accuracy: 6.2539e-04 - lr: 0.0000e+00
Epoch 23716/2000000
38/38 [==============================] - 0s 3ms/step - loss: 0.7927 - accuracy: 0.0000e+00 - val_loss: 0.4530 - val_accuracy: 6.2539e-04 - lr: 0.0000e+00
Epoch 23717/2000000
38/38 [==============================] - 0s 3ms/step - loss: 0.7927 - accuracy: 0.0000e+00 - val_loss: 0.4530 - val_accuracy: 6.2539e-04 - lr: 0.0000e+00
Epoch 23718/2000000
38/38 [==============================] - 0s 3ms/step - loss: 0.7927 - accuracy: 0.0000e+00 - val_loss: 0.4530 

IOPub message rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_msg_rate_limit`.

Current values:
ServerApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
ServerApp.rate_limit_window=3.0 (secs)



38/38 [==============================] - 0s 3ms/step - loss: 0.7927 - accuracy: 0.0000e+00 - val_loss: 0.4530 - val_accuracy: 6.2539e-04 - lr: 0.0000e+00
Epoch 43893/2000000
38/38 [==============================] - 0s 2ms/step - loss: 0.7927 - accuracy: 0.0000e+00 - val_loss: 0.4530 - val_accuracy: 6.2539e-04 - lr: 0.0000e+00
Epoch 43894/2000000
38/38 [==============================] - 0s 2ms/step - loss: 0.7927 - accuracy: 0.0000e+00 - val_loss: 0.4530 - val_accuracy: 6.2539e-04 - lr: 0.0000e+00
Epoch 43895/2000000
38/38 [==============================] - 0s 3ms/step - loss: 0.7927 - accuracy: 0.0000e+00 - val_loss: 0.4530 - val_accuracy: 6.2539e-04 - lr: 0.0000e+00
Epoch 43896/2000000
38/38 [==============================] - 0s 3ms/step - loss: 0.7927 - accuracy: 0.0000e+00 - val_loss: 0.4530 - val_accuracy: 6.2539e-04 - lr: 0.0000e+00
Epoch 43897/2000000
38/38 [==============================] - 0s 3ms/step - loss: 0.7927 - accuracy: 0.0000e+00 - val_loss: 0.4530 - val_accuracy: 6.25

IOPub message rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_msg_rate_limit`.

Current values:
ServerApp.iopub_msg_rate_limit=1000.0 (msgs/sec)
ServerApp.rate_limit_window=3.0 (secs)



38/38 [==============================] - 0s 3ms/step - loss: 0.7927 - accuracy: 0.0000e+00 - val_loss: 0.4530 - val_accuracy: 6.2539e-04 - lr: 0.0000e+00
Epoch 47544/2000000
38/38 [==============================] - 0s 3ms/step - loss: 0.7927 - accuracy: 0.0000e+00 - val_loss: 0.4530 - val_accuracy: 6.2539e-04 - lr: 0.0000e+00
Epoch 47545/2000000
38/38 [==============================] - 0s 3ms/step - loss: 0.7927 - accuracy: 0.0000e+00 - val_loss: 0.4530 - val_accuracy: 6.2539e-04 - lr: 0.0000e+00
Epoch 47546/2000000
38/38 [==============================] - 0s 3ms/step - loss: 0.7927 - accuracy: 0.0000e+00 - val_loss: 0.4530 - val_accuracy: 6.2539e-04 - lr: 0.0000e+00
Epoch 47547/2000000
38/38 [==============================] - 0s 3ms/step - loss: 0.7927 - accuracy: 0.0000e+00 - val_loss: 0.4530 - val_accuracy: 6.2539e-04 - lr: 0.0000e+00
Epoch 47548/2000000
38/38 [==============================] - 0s 3ms/step - loss: 0.7927 - accuracy: 0.0000e+00 - val_loss: 0.4530 - val_accuracy: 6.25